# 1. Introduction

In the last homework, you implemented a robust face recognition system given frontal view, aligned face images. However, in reality, the images are not always perfectly aligned. In this homework, we tackle the misalignment problem by using sparse and low-rank decomposition of linear correlated images (such as face images from slightly different viewpoints).

For example, the following code show what is the expected outcome:

The input is a set of face images, with moderate misalignment

In [ ]:
!pip install wget
import wget
wget.download("https://tinyurl.com/yp3nsarj", './data.zip')
!unzip -q data.zip

In [ ]:
import os
import cv2
from matplotlib import pyplot as plt
demo_folder = './data/demo/'
demo_D = cv2.imread(os.path.join(demo_folder, 'D.png'))
plt.figure(figsize=(20,10))
plt.axis('off')
plt.imshow(demo_D)

You need to find its low-rank and sparse error decompositions as the following examples shows:

In [ ]:
demo_A = cv2.imread(os.path.join(demo_folder, 'A.png'))
demo_E = cv2.imread(os.path.join(demo_folder, 'E.png'))
plt.figure(figsize=(20,10))
plt.axis('off')
plt.subplot(1, 2, 1)
plt.imshow(demo_A)
plt.subplot(1, 2, 2)
plt.imshow(demo_E)

Note that now the faces are well aligned.

# 2. Formulation and Approach

The critical point here is how to deal with the deformations between the misaligned images and the aligned faces.

The intuition here is conceptually very simple: if the face images are well aligned, they should have a linear structure if we view them as vectors (This phenomenon is also the foundation of your homework 2 - robust face recognition). In mathematical language, for $i$-th datapoint in our dataset, we assume $$I_i \circ \tau_i = (I^0_i + E_i)$$ where $I_i$ is the original image, $\tau_i$ is the transformation make the image aligned, $I_i^0$ is the aligned image, and $E_i$ is the sparse error.

Utilizing the property that $I_i^0$ should be linearly correlated, $A = [I_0^0 |  I_1^0 | \cdots | I_n^0]$ should be a low-rank matrix.

Therefore we can write the problem as the following:

$$\min_{A,E,\tau} \text{rank}(A) \;\;\; \text{s.t.} \;\;\; D \circ \tau = A + E, ||E||_0 < k$$

The above formulation is NP-hard. Instead, we can solve the following relaxation one using what we learned in this class:

$$\min_{A,E,\tau} ||A||_* + \lambda ||E||_1 \;\;\; \text{s.t.} \;\;\; D\circ \tau = A+E$$

The main task of this homework is to learn and solve the above problems. You are required to understand **Section 3.2** and **Algorithm 2** of https://people.eecs.berkeley.edu/~yima/matrix-rank/Files/RASL_CVPR10.pdf and fill out the following blanks.

# 3. Data Preparation and Visualization

## 3.1 Data Loading

In [ ]:
import numpy as np
raw_im_h, raw_im_w = 250, 250
im_h, im_w = 80, 60
canonical_ref_point = np.array([[5, 55], [32, 32]])

In [ ]:
from glob import glob
import scipy.io as sio

def load_lfw_data(subject_name):
    image_dir = os.path.join('./data/LFW/', subject_name)
    image_list = sorted(glob(os.path.join(image_dir, '*.jpg')))
    image_array = np.zeros((0, raw_im_h, raw_im_w))
    ref_point_array = np.zeros((0, 2, 2))
    for image_name in image_list:
        im = cv2.cvtColor(cv2.imread(image_name), cv2.COLOR_BGR2GRAY)
        ref_point = sio.loadmat(image_name.replace('.jpg', '-points.mat'))['points']
        image_array = np.concatenate([image_array, im[np.newaxis, :]], axis=0)
        ref_point_array = np.concatenate([ref_point_array, ref_point[np.newaxis, :]], axis=0)
    return image_array, ref_point_array

Ariel_Sharon is one subject in the LFW dataset, here we use it for illustration purpose. You are encouraged to try different subject in your algorithm if time allowed. Other options include:

'Gloria_Macapagal_Arroyo', 'Jennifer_Capriati', 'Laura_Bush',  
'Serena_Williams', 'Barack_Obama', 'Ariel_Sharon', 
'Arnold_Schwarzenegger', 'Colin_Powell', 'Donald_Rumsfeld',
'George_W_Bush', 'Gerhard_Schroeder', 'Hugo_Chavez',
'Jacques_Chirac', 'Jean_Chretien', 'John_Ashcroft',
'Junichiro_Koizumi', 'Lleyton_Hewitt', 'Luiz_Inacio_Lula_da_Silva', 
'Tony_Blair', 'Vladimir_Putin'

In [ ]:
image_array, ref_point_array = load_lfw_data('George_W_Bush')

The reference points here is the eye points of the subject. This is because this algorithm cannot deal with global, large deformations. Therefore, for complex images like face, we need to restrict the search region a little bit.

Some examples are shown in the following:

In [ ]:
plt.figure(figsize=(20,10))
for i in range(1, 6):
    plt.subplot(1, 5, i)
    plt.imshow(image_array[i], cmap='gray')
    plt.scatter(ref_point_array[i, 0], ref_point_array[i, 1], s=30)

## 3.2 Crop and Resize to Face-centric Images

In this section, we compute a face centric image patch according to the predefined reference points.

The idea is: we want to calculate an affine transformation $T_i$ for each image, such that the canonical_ref_point will be transformed to the eye point of raw image after applying $T_i$. The way of compute $T_i$ is not required and given as follows:

In [ ]:
def similarity_transform(points1, points2):
    # points2 = ref_point_array[0]
    # points1 = ref_points
    delta = np.array([[0, -1], [1, 0]])
    points1 = np.hstack([points1, (points1[:, 0] + delta @ (points1[:, 1] - points1[:, 0]))[:, None]])
    points2 = np.hstack([points2, (points2[:, 0] + delta @ (points2[:, 1] - points2[:, 0]))[:, None]])
    points1 = np.vstack([points1, np.ones((1, 3))])
    D = np.kron(np.eye(2), points1.T)
    A_tr_vec = np.linalg.inv(D) @ np.vstack([points2[[0], :].T, points2[[1], :].T]);
    A = np.inf * np.ones((2, 3))
    A[0, :] = A_tr_vec[:3].T
    A[1, :] = A_tr_vec[3:].T
    return A

In [ ]:
taus = np.zeros((0, 2, 3))
for idx, ref_point in enumerate(ref_point_array):
    trans = similarity_transform(canonical_ref_point, ref_point)
    taus = np.concatenate([taus, trans[np.newaxis, :]])

Using this transformation, we can crop and resize raw images to a face-centric images, one examples are shown below.

In [ ]:
warp_im = cv2.warpAffine(image_array[0], 
                         cv2.invertAffineTransform(taus[0]), 
                         dsize=(im_w, im_h))
plt.subplot(1, 2, 1)
plt.imshow(image_array[0], cmap='gray')
plt.subplot(1, 2, 2)
plt.imshow(warp_im, cmap='gray')


Note that, here the ```transformations``` array is the initial transformation, although it gives you a face centric image, but it do not align the image well. In the next step, you will iteratively update the $\tau$ and get aligned face images.

# 4. Your Tasks

## 4.1 Task 1: Complete the outer loop of RASL algorithm
Please use the helper functions given below to complete the missing blocks in ```image_alignment()```. Each block to complete requires only 1-2 lines of code.

## 4.2 Task 2: Complete the inner loop of RASL algorithm
Please write a the function ```apg(**kwargs)``` which is used in the inner loop.

---

To compute the Jacobian, it's helpful to use the x-direction and y-direction gradient of the images, which are given in the following code:



In [ ]:
from scipy.ndimage import gaussian_filter, sobel
def pre_process_image(im):
    im_gaussian = gaussian_filter(im, sigma=1, truncate=3)
    dy = sobel(im_gaussian, axis=0, mode='constant')
    dx = sobel(im_gaussian, axis=1, mode='constant')
    return im_gaussian, dx, dy

In [ ]:
im_gaussian, dx, dy = pre_process_image(image_array[0])
plt.subplot(2, 2, 1)
plt.imshow(image_array[0], cmap='gray')
plt.subplot(2, 2, 2)
plt.imshow(im_gaussian, cmap='gray')
plt.subplot(2, 2, 3)
plt.imshow(dx, cmap='gray')
plt.subplot(2, 2, 4)
plt.imshow(dy, cmap='gray')

In [ ]:
def compute_jacobian(dx, dy, tau):
    # Compute the jacobian matrix with respect to 
    # image and affine transformation parameters

    # calculate \nabla I_x & \nabla I_y
    dx_warp_im = cv2.warpAffine(dx, cv2.invertAffineTransform(tau), dsize=(im_w, im_h))
    dy_warp_im = cv2.warpAffine(dy, cv2.invertAffineTransform(tau), dsize=(im_w, im_h))
    # calculate \nabla W_p & \nabla I_y
    dx_p = np.array([np.array(range(dx_warp_im.shape[1])),]*dx_warp_im.shape[0])
    dy_p = np.array([np.array(range(dy_warp_im.shape[0])),]*dx_warp_im.shape[1]).transpose()
    # calculate jacobian matrix
    im_len = dx_warp_im.shape[0] * dx_warp_im.shape[1]
    J = np.reshape(np.multiply(dx_warp_im, dx_p), (im_len, -1))
    J = np.concatenate([J, np.reshape(np.multiply(dy_warp_im, dx_p), (im_len, -1))], axis=1)
    J = np.concatenate([J, np.reshape(np.multiply(dx_warp_im, dy_p), (im_len, -1))], axis=1)
    J = np.concatenate([J, np.reshape(np.multiply(dy_warp_im, dy_p), (im_len, -1))], axis=1)
    J = np.concatenate([J, np.reshape(dx_warp_im, (im_len, -1))], axis=1)
    J = np.concatenate([J, np.reshape(dy_warp_im, (im_len, -1))], axis=1)
    return J

In [ ]:
from numpy import linalg as LA
def image_array_warpAffine(image_array, taus, normalize=True):
    im_warp_array = np.zeros((image_array.shape[0], im_h * im_w))
    for idx in range(image_array.shape[0]):
        # warp image
        im_warp_array_idx = cv2.warpAffine(image_array[idx], cv2.invertAffineTransform(taus[idx]), dsize=(im_w, im_h))
        im_len = im_warp_array_idx.shape[0] * im_warp_array_idx.shape[1]
        
        if normalize:
            im_warp_array_idx = np.reshape(im_warp_array_idx, (im_len, -1))
            im_warp_array_idx = im_warp_array_idx / LA.norm(im_warp_array_idx, 'fro')
            
        im_warp_array[idx] = np.reshape(im_warp_array_idx, (im_len, ))

    return im_warp_array

In [ ]:
# save dx, dy
im_dx_array = np.zeros_like(image_array)
im_dy_array = np.zeros_like(image_array)
for idx in range(image_array.shape[0]):
    _, im_dx_array[idx], im_dy_array = pre_process_image(image_array[idx])


In [ ]:
## Soft thresholding (proximal operator for real-valued lambda-scaled L1 norm)
def soft_thresh(x, lambd):
    return np.maximum(x - lambd, np.zeros_like(x)) - np.maximum(- lambd - x, np.zeros_like(x))

In [ ]:
def image_alignment(image_array, taus):

    converged = False
    while not converged:      
        # step 1: compute Jacobian matrices w.r.t. transformation
        J_array = np.zeros((image_array.shape[0], im_h * im_w, 6))
        Dotau_unnorm = image_array_warpAffine(image_array, taus, normalize=False)
        for idx_Jacobian in range(image_array.shape[0]):
            ########### Start your code ############
            # compute J_idx
            J_idx = 
            ########### End your code ############
            x_idx = Dotau_unnorm[idx_Jacobian]
            x_idx = np.reshape(x_idx, (x_idx.shape[0], -1))
            x_norm = LA.norm(x_idx, 'fro')
            J_array[idx_Jacobian] = J_idx / x_norm - ((x_idx @ x_idx.transpose()) @ J_idx) / (x_norm * x_norm * x_norm)
      
        # step 2: warp and normalize the images
        ########### Start your code ############
        
        ########### End your code ############
        
        # step 3: solve the linearized convex optimization
        
        ########### Start your code ############
        A, E, delta_taus = apg(**kwargs)
        ########### End your code ############
        
        delta_taus = delta_taus.transpose()
        delta_taus_update = np.zeros_like(taus)
        for idx in range(taus.shape[0]):
            delta_taus_update[idx] = np.reshape(delta_taus[idx], (2, -1))
        # step 4: update transformations
        ########### Start your code ############
        
        ########### End your code ############
        
    return A, E, taus

In [ ]:
taus = np.zeros((0, 2, 3))
for idx, ref_point in enumerate(ref_point_array):
    trans = similarity_transform(canonical_ref_point, ref_point)
    taus = np.concatenate([taus, trans[np.newaxis, :]])

In [ ]:
A, E, tau_star = image_alignment(image_array, taus)

Your final delivery should be a visualization of your aligned images.



In [ ]:
im_warp_mtx = np.zeros((35, 80, 60))
for idx in range(image_array.shape[0]):
    im_warp_mtx[idx] = np.reshape(A.transpose()[idx], (80, 60))

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

w=10
h=10
plt.axis('off')
fig=plt.figure(figsize=(80, 60))
columns = 7
rows = 5
plt.rcParams['figure.dpi'] = 20
for i in range(1, columns*rows + 1):
    fig.add_subplot(rows, columns, i)
    plt.axis('off')
    plt.imshow(im_warp_mtx[i-1], cmap='gray')
plt.show()